In [1]:
import numpy as np
import pandas as pd
import folium
import requests
import polyline
from sklearn.cluster import KMeans

In [2]:
data = pd.read_excel('Provinces.xlsx')
coordinates = data[['Latitude', 'Longitude']].values

# Option 1

In [3]:
warehouses = {
    'HCMC': (10.634706, 106.7206625),
    'Hanoi': (20.9734367, 106.0280013)
}

In [4]:
# Function to find the nearest warehouse for each demand point for option 1
def find_nearest_warehouse(point, warehouses, graphhopper_key):
    nearest = None
    min_distance = float('inf')
    for name, location in warehouses.items():
        route = get_route(location, point, graphhopper_key)
        if route:
            dist = sum(np.linalg.norm(np.array(route[i]) - np.array(route[i + 1])) for i in range(len(route) - 1))
            if dist < min_distance:
                nearest = name
                min_distance = dist
    return nearest

# Function to get routing data from GraphHopper for both option 1 and 2
def get_route(start, end, graphhopper_key):
    url = "https://graphhopper.com/api/1/route"
    params = {
        'point': [f"{start[0]},{start[1]}", f"{end[0]},{end[1]}"],
        'vehicle': 'car',
        'key': graphhopper_key,
        'instructions': False,
        'points_encoded': True
    }
    response = requests.get(url, params=params)
    if response.status_code == 200:
        response_data = response.json()
        if 'paths' in response_data:
            route_polyline = response_data['paths'][0]['points']
            return polyline.decode(route_polyline)
    return None

In [6]:
map_option_1 = folium.Map(location=[14.058324, 108.277199], zoom_start=6, tiles='CartoDB Voyager')

# Add warehouse markers
for name, location in warehouses.items():
    folium.Marker(
        location=location,
        popup=name,
        icon=folium.Icon(icon='industry', color='red', prefix='fa')
    ).add_to(map_option_1)

# Add demand points and routes
graphhopper_key = 'e5059108-7bef-4f9f-8d45-186941e5e089' 
for point in coordinates:
    nearest_warehouse = find_nearest_warehouse(point, warehouses, graphhopper_key)
    if nearest_warehouse:
        warehouse_location = warehouses[nearest_warehouse]
        route = get_route(warehouse_location, point, graphhopper_key)
        if route:
            folium.PolyLine(locations=route, weight=2, color='blue').add_to(map_option_1)
        else:
            folium.PolyLine(locations=[warehouse_location, point], weight=2, color='gray').add_to(map_option_1)
        folium.CircleMarker(
            location=point,
            radius=3,
            color='blue',
            fill=True,
            fill_color='blue',
            popup=f'Demand Point'
        ).add_to(map_option_1)

map_option_1


In [7]:
# Calculate distance between two points
from geopy.distance import geodesic
results = []
def calculate_distance(start, end):
    return geodesic(start, end).kilometers
for i, row in data.iterrows():
    point = (row['Latitude'], row['Longitude'])
    province_name = row['Province']
    nearest_warehouse_name = find_nearest_warehouse(point, warehouses,graphhopper_key)
    nearest_warehouse_location = warehouses[nearest_warehouse_name]
    distance = calculate_distance(point, nearest_warehouse_location)
    results.append({
        'Province': province_name,
        'Latitude': row['Latitude'],
        'Longitude': row['Longitude'],
        'Nearest Warehouse': nearest_warehouse_name,
        'Distance (km)': distance
    })

results_df = pd.DataFrame(results)
results_df

Province   Latitude   Longitude Nearest Warehouse  Distance (km)
0            An Giang  10.390544  105.433752              HCMC     143.434551
1   Bà Rịa - Vũng Tàu  10.520962  107.224499              HCMC      56.557031
2          Bình Dương  11.112894  106.700216              HCMC      52.941465
3          Bình Phước  11.718505  106.854646              HCMC     120.775355
4          Bình Thuận  10.989323  108.083244              HCMC     154.082834
..                ...        ...         ...               ...            ...
58            Đà Nẵng  16.056071  108.175061             Hanoi     589.581688
59            Đắk Lắk  12.788882  108.216809              HCMC     288.763605
60           Đắk Nông  12.221352  107.587761              HCMC     199.392343
61           Đồng Nai  10.984279  107.148489              HCMC      60.696650
62          Đồng Tháp  10.553430  105.625077              HCMC     120.231185

[63 rows x 5 columns]

# Option 2

In [8]:
# Define warehouse locations
warehouses_2 = {
    'Hanoi': (21.028511, 105.804817),
    'HCMC': (10.762622, 106.660172),
    'Da Nang': (16.054407, 108.202167)
}

In [9]:
# Function to find the nearest warehouse for each centroid in option 2
def find_nearest_warehouse_2(centroid, warehouses):
    nearest = None
    min_distance = float('inf')
    for name, location in warehouses.items():
        dist = np.linalg.norm(np.array(centroid) - np.array(location))
        if dist < min_distance:
            nearest = name
            min_distance = dist
    return nearest


In [10]:
# Apply K-means clustering
kmeans = KMeans(n_clusters=3, random_state=0).fit(coordinates)
centroids = kmeans.cluster_centers_
adjusted_centroids = {find_nearest_warehouse_2(centroid, warehouses_2): centroid for centroid in centroids}

map_option_2 = folium.Map(location=[14.058324, 108.277199], zoom_start=6, tiles='CartoDB Voyager')

# Add warehouse markers
for name, location in warehouses_2.items():
    folium.Marker(
        location=location,
        popup=name,
        icon=folium.Icon(icon='industry', color='red', prefix='fa')
    ).add_to(map_option_2)

In [11]:
# Add routes and demand points
graphhopper_key = 'e5059108-7bef-4f9f-8d45-186941e5e089'
for i, centroid in enumerate(centroids):
    cluster_points = coordinates[kmeans.labels_ == i]
    warehouse_name = find_nearest_warehouse_2(centroid, warehouses_2)
    warehouse_location = warehouses_2[warehouse_name]
    color = ['blue', 'green', 'orange'][i % 3]
    for point in cluster_points:
        route = get_route(warehouse_location, point, graphhopper_key)
        if route:
            folium.PolyLine(locations=route, weight=2, color=color).add_to(map_option_2)
        else:
            folium.PolyLine(locations=[warehouse_location, point], weight=2, color='gray').add_to(map_option_2)
        folium.CircleMarker(
            location=point,
            radius=3,
            color=color,
            fill=True,
            fill_color=color,
            popup='Demand Point'
        ).add_to(map_option_2)
map_option_2

In [13]:
from geopy.distance import geodesic
results_2 = []
def calculate_distance(start, end):
    return geodesic(start, end).kilometers
for i, row in data.iterrows():
    point = (row['Latitude'], row['Longitude'])
    province_name = row['Province']
    nearest_warehouse_name = find_nearest_warehouse_2(point, warehouses_2)
    nearest_warehouse_location = warehouses_2[nearest_warehouse_name]
    distance = calculate_distance(point, nearest_warehouse_location)
    results_2.append({
        'Province': province_name,
        'Latitude': row['Latitude'],
        'Longitude': row['Longitude'],
        'Nearest Warehouse': nearest_warehouse_name,
        'Distance (km)': distance
    })

df_results_2 = pd.DataFrame(results_2)
df_results_2


Province   Latitude   Longitude Nearest Warehouse  Distance (km)
0            An Giang  10.390544  105.433752              HCMC     140.387916
1   Bà Rịa - Vũng Tàu  10.520962  107.224499              HCMC      67.284660
2          Bình Dương  11.112894  106.700216              HCMC      38.991597
3          Bình Phước  11.718505  106.854646              HCMC     107.847821
4          Bình Thuận  10.989323  108.083244              HCMC     157.596245
..                ...        ...         ...               ...            ...
58            Đà Nẵng  16.056071  108.175061           Da Nang       2.906311
59            Đắk Lắk  12.788882  108.216809              HCMC     281.109983
60           Đắk Nông  12.221352  107.587761              HCMC     190.470658
61           Đồng Nai  10.984279  107.148489              HCMC      58.750281
62          Đồng Tháp  10.553430  105.625077              HCMC     115.590951

[63 rows x 5 columns]